In [95]:
import altair as alt
from vega_datasets import data
import json
import pandas as pd
import numpy as np

alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [96]:

# Opening JSON file
f = open(r'../data/maps/county003wtown.json',)
# returns JSON object as a dictionary
mass_json = json.load(f)
# Closing file
f.close()
# reading dictionary into altair data format
mass_data = alt.Data(values=mass_json)

In [97]:
# Opening JSON points file
fpts = open(r'../data/maps/points.json',)
 
# returns JSON object as a dictionary
wtown_points = json.load(fpts)

# Closing file
fpts.close()

# read data into nice dataframe
df = pd.json_normalize(wtown_points['features'])
coords = pd.DataFrame(df["geometry.coordinates"].to_list(), columns=['lat', 'lon'])
props = df[["properties.type","properties.name"]]
props = props.rename(columns={"properties.type": "type", "properties.name": "name"}, errors="raise")

props.replace("", np.nan, inplace=True)
props.dropna(subset = ["name"], inplace=True)
props.dropna(subset = ["type"], inplace=True)

points_data = pd.merge(coords, props , how="outer", left_index = True, right_index=True)
points_data.replace("", np.nan, inplace=True)
points_data.dropna(inplace=True)

In [98]:
# Opening road JSON file
froad = open(r'../data/maps/roads.json',)
 
# load JSON road data
wtown_roads = json.load(froad)

# close road JSON file
froad.close()

# split into geometry and type, then properties for tooltip
geotemp = pd.json_normalize(wtown_roads['features'], max_level = 0)
proptemp = pd.json_normalize(wtown_roads['features'], max_level = 1)

proptemp.rename(columns = {"properties.name": 'st_name',
                           "properties.type": 'road_type',
                           "properties.oneway":'oneway', 
                           "properties.bridge":'bridge',
                            "properties.maxspeed":'max_speed'}, inplace = True)

# merge so the data makes sense
roadpd = pd.merge(geotemp.iloc[:,0:2], 
                  proptemp.loc[:,['st_name','road_type','oneway','bridge','max_speed']],
                  left_index = True, right_index = True)

roadpd.replace(np.nan,0, inplace=True)

In [99]:
address_geom = pd.read_csv(r'../data/addresses_geometry.csv', index_col=0)
address_geom['names'].str.replace("_", " ")
address_geom.replace(np.nan," ", inplace=True)
address_geom['st_address'] = address_geom['nums'].astype('str')+ ' ' +address_geom['names'].str.replace("_", " ")
address_geom['st_address'] = address_geom['st_address'].str.replace('.0','',regex=False).str.title()

address_geom = address_geom.drop(columns = ['names','nums','geometry'])
address_geom = address_geom[(address_geom['lat'] < 42.745071) & (address_geom['lat'] > 42.630525)]
address_geom = address_geom[(address_geom['lon'] > -73.307080) & (address_geom['lon'] < -73.171065)]


incidents = pd.read_csv(r'../data/parsed_logs_2019.csv', index_col=0)
incidents['call_taker'] = incidents['call_taker'].str.title()
new = incidents.merge(address_geom, left_on='call_number', right_on='call_number')

In [110]:
addr = pd.read_csv(r'../data/addresses_geometry_white_oaks.csv', index_col=0)
addr[['lat','lon']] = addr['geometry'].str.replace("POINT (",'',regex=False).str.replace(")",'',regex=False).str.split(' ',expand=True)
addr[['lat','lon']] = addr[['lat','lon']].astype('float')

addr.replace(np.nan," ", inplace=True)
addr['st_address'] = addr['nums'].astype('str')+ ' ' +addr['names'].str.replace("_", " ")
# addr['st_address'] = addr['st_address'].str.replace('.0','',regex=False).str.title()


addr = addr.drop(columns = ['names','nums','geometry'])

addr = addr[(addr['lat'] < 42.745071) & (addr['lat'] > 42.630525) & 
            (addr['lon'] > -73.307080) & (addr['lon'] < -73.171065)]

incidents = pd.read_csv(r'../data/parsed_logs_2019.csv', index_col=0)
incidents.replace(np.nan," ", inplace=True)

incidents['call_taker'] = incidents['call_taker'].str.title()
incidents['call_taker'].replace(' ', 'Unknown', regex=False, inplace=True)

In [111]:
reasons = incidents['call_reasons'].unique()

def label_incident(row):
    if (row['call_reasons'][0]== 'I'):
        return 1
    elif (row['call_reasons'][0]== '9'):
        return 2
    elif (row['call_reasons'][0]== 'P'):
        return 3
    elif (row['call_reasons'][0]== 'W'):
        return 4
    elif (row['call_reasons'][0]== 'O'):
        return 5
    elif (row['call_reasons'][0]== 'R'):
        return 5
    else :
        return 6
    
incidents['init_bin'] = incidents.apply(lambda row: label_incident(row), axis=1)  
new = incidents.merge(addr, left_on='call_number', right_on='call_number')

In [171]:
# Map of Williamstown
officersort = ['Unknown','Patrol Tania Hernandez', 'Patrol David Jennings, D','Sergeant Scott E Mcgowan','Patrolman Michael J Ziemba Jr','Patrol Kalvin Dziedziak','Dispatcher Laurie Tuper','Patrol John J Mcconnell Jr','Patrol Shuan N William','Patrol Brad Sacco','Sergeant David R Lemieux','Patrol Anthony M Duprat','Patrol Kevin P Garner','Chief Kyle J Johnson','Patrolman Scott Skorupski','Dispatcher William C Jennings Jr','Sergeant Paul D Thompson','Patrol Craig A Eichhammer','Michael Strizzi','All Equipment Police Department','Dispatcher Christine Lemoine']
officercsort = ['Patrol Tania Hernandez', 'Patrol David Jennings, D','Sergeant Scott E Mcgowan','Patrolman Michael J Ziemba Jr','Patrol Kalvin Dziedziak','Unknown','All Equipment Police Department','Dispatcher Laurie Tuper','Patrol John J Mcconnell Jr','Patrol Shuan N William','Patrol Brad Sacco','Sergeant David R Lemieux','Patrol Anthony M Duprat','Patrol Kevin P Garner','Chief Kyle J Johnson','Patrolman Scott Skorupski','Dispatcher William C Jennings Jr','Sergeant Paul D Thompson','Patrol Craig A Eichhammer','Michael Strizzi','Dispatcher Christine Lemoine']

hover_incident = alt.selection_single(
    on="mouseover", nearest=True, fields=["st_address"], empty="none"
)
officerscale = alt.Scale(scheme='category20')


multi = alt.selection_multi(encodings = ['y'],resolve = 'intersect')

background = alt.Chart(mass_data).mark_geoshape(
    fill='lightgray',
    stroke='lightgray'
).properties(
    width=600,
    height=800,
).project('mercator')

road_layer = alt.Chart(roadpd).mark_geoshape(
    fill='none',
    stroke = 'darkgray',
    strokeWidth=2
).properties(
    width=600,
    height=800
).project(
    'mercator'
)

points_layer = alt.Chart(new).mark_circle(
    size=100,
    color = 'lightblue'
).encode(
    color = alt.condition(hover_incident, 
                          alt.value('white'), 
                          alt.Color('call_taker:N', scale=officerscale, sort=officercsort[::-1])),
#     opacity = 'init_bin:Q',
    longitude='lon:Q',
    latitude='lat:Q',
    tooltip = ['call_number','st_address','call_taker',"call_actions"]
).add_selection(
    hover_incident
).transform_filter(multi)


c = alt.Chart(new).mark_bar().encode(
    alt.X('count()', axis=alt.Axis(title="Number of Responses", titleFontSize=20,labels=True,labelFontSize =14)),
    alt.Y('call_taker:N', sort=officersort[::-1], axis=alt.Axis(title='', labelFontSize=14, labelLimit = 350)),
    alt.Color('call_taker:N', scale=officerscale, sort=officercsort[::-1], legend=None),
).properties(width=200,height=400)

hist = alt.layer(
    c.add_selection(multi).encode(
        color=alt.condition(
            multi, alt.Color('call_taker:N', scale=officerscale, sort=officercsort[::-1]),
            alt.value('lightgrey'))
    ),
    c.transform_filter(multi)
)

map = (background + road_layer + points_layer)

map.properties(
    title = 'Williamstown Police Responses 2019',
    titleFontSize = 20)

alt.hconcat(hist, map, autosize="pad").configure_view(strokeOpacity=0)




alt.HConcatChart(...)

In [170]:
# # Boolean selection for format changes
# callactions = new['call_actions'].unique()
# input_checkbox = alt.binding_radio(options=callactions)
# checkbox_selection = alt.selection_single(bind=input_checkbox, name="Response Type", fields=["call_actions:N"])

# mapfilt = map.add_selection(
#         checkbox_selection
# ).properties(title="Checkbox Formatting").transform_filter(checkbox_selection)

# check = hist.transform_filter(checkbox_selection)

# alt.hconcat( check, mapfilt, autosize="pad").configure_view(strokeOpacity=0)
